#### Ce Notebook contient les differentes fonctions necessaires pour recuperer les données que nous souhaitons analyser sur la plateforme dicames.online

Les differentes fonctions que nous avons implementées sont :
- **datas_sous_communaute**
- **liste sous_communaute**
- **construire_df**
- **data_all**

#### La fonction **datas_sous_communaute**

Cette fonction prend en paramètre le nom d'une sous_communauté, son URL ansi que le nom de la communauté(pays) à la quelle elle appartient. Elle renvoit un dataframe contenant la sous_communauté, toutes ses collections et toutes les URLs de ces collections.

In [1]:
import requests
from bs4 import BeautifulSoup
import pandas as pd

In [3]:


""" La fonction datas_sous_communaute prend en paramètre le nom et le lien d'une sous communauté pour 
un pays donné dans dicames.online et renvoie un dataframe contenant toutes les collections
de cette sous-communauté et leurs liens """

def datas_sous_communaute(nom_sous_communaute, url_sous_communaute, nom_communaute):

    #Listes contenant les noms des sous-communautés des collections et leurs liens. Elles seront
    #utilisées pour créer le dataframe
    nom_sous_communaute_list = []
    collections_list = []
    url_sous_communaute_list = []
    pays_list = []

    #Une requête vers la page contenant les collections pour la sous-communauté
    response = requests.get(url_sous_communaute)
    if response.status_code == 200:
        soup = BeautifulSoup(response.content, "html.parser")
        #On recupère les collections et leurs liens
        listgroup = soup.find_all("h4", class_="list-group-item-heading")
        #On crée une liste qui contient le nom de la sous-communauté (repété), une autre liste contenant 
        #les collections et enfin une liste contenant les liens de chaque collection.
        for element in listgroup:
            cells = element.find("a", class_="")
            nom_sous_communaute_list.append(nom_sous_communaute)
            collections_list.append(cells.text.strip())
            url_sous_communaute_list.append(cells["href"])
            pays_list.append(nom_communaute)
        #On crée un dictionnaire avec nos trois précédentes listes et ensuite on crée un dataframe à partir de 
        #ce dictionnaire
        dict = {"Sous Communauté" : nom_sous_communaute_list, "Collections": collections_list, "URL": url_sous_communaute_list, "Pays": pays_list}
        df = pd.DataFrame(dict)
    else:
        print(f"Erreur : Code de statut {response.status_code} pour {url_sous_communaute}")
    #print(df)
    return df

#### La fonction **liste_sous_communaute**

Cette fonction a pour objectifs de recupérer pour une communauté donnée, les noms et les lines de toutes ses sous-communautés pour ensuite les passer à la fonctions datas_sous_communauté. L'objectif final etant de parcourir toutes ces liens et d'en recupérer les données.

In [4]:
""" La fonction liste_sous_communauté prend en paramètre le lien vers une communauté(pays), recupère toutes les sous-communautés
de la communauté avec leurs liens et fait appel à la fonction datas_sous_communaute pour créer enfin un dataframe contenant toutes les sous-
communautés associées à leurs collections. """

def liste_sous_communaute(url_communaute, nom_communaute):

    #la liste qui contient tous les dataframes renvoyés par la fonction datas_sous_communaute
    df_list = []

    response = requests.get(url_communaute)
    if response.status_code == 200:
        print ("Traitement de données pour le " + nom_communaute + " .Ceci pourrait prendre plusieurs minutes, veuillez Patienter...")
        soup = BeautifulSoup(response.content, "html.parser")
        listgroup = soup.find_all("h4", class_="list-group-item-heading")
        #On récupère toutes les sous-communautés et leurs liens
        for element in listgroup:
            cells = element.find("a", class_="")
            nom_sous_communaute = cells.text.strip()
            url_sous_communaute =  "https://dicames.online" + cells["href"] 
            df = datas_sous_communaute(nom_sous_communaute, url_sous_communaute, nom_communaute)
            #la fonction datas_sous_communaute renvoie à chaque iterration un dataframe pour une sous-communauté donnée
            #Chaque dataframe est ajouté à une liste
            df_list.append(df)
            #On utilise cette liste pour faire la concatenation de tous les dataframes crées par datas_sous_communaute
        result = pd.concat(df_list)
    else:
        print(f"Erreur : Code de statut {response.status_code} pour {url_communaute}")
    return result

#### La fonction **construire_df**

Cette fonction fait usage du dataframe renvoyé par la fonction liste_sous_communaute. L'objectif est de parcourir ce dataframe ligne par ligne et de transformer chaque ligne en liste. La fonction construire_df devra à chaque iterration du dataframe, prendre une liste en parametre et renvoyer un dataframe contenant les données relatives à la communauté dont les données sont passées dans la liste.


In [5]:
"""
    La fonction contruire_df prend en paramètres une liste contenant le nom de la sous_communaute, le lien d'une collection correpondant 
    à cette sous-communaute, le nom

"""
def construire_df(myList = [], *args):
    
    
    #myList[2] contient l'URL de la collection
    response = requests.get("https://dicames.online/" + myList[2])
    soup = BeautifulSoup(response.content, 'html.parser')
    tableau = soup.find('table', class_='table')
    if(tableau):
    # Extraire les données du premier tableau
        donnees = []
        for ligne in soup.find_all('tr'):
            ligne_data = []
            ligne_data.append(myList[0]) #myList[0] contient l'index
            ligne_data.append(myList[1]) #myList[1] contient le nom de la sous_communaute
            ligne_data.append(myList[3]) #myList[1] contient le nom de la communaute
            for cellule in ligne.find_all('td'):
                valeur = cellule.text.strip()
                ligne_data.append(valeur)
                #Ici on ajoute les données de la collection (Date de publication, Titre de l'oeuvre, Auteur(s))
            donnees.append(ligne_data)
          
    #On recupère le lien vers la page suivante
        nav_link = soup.find_all('div', 'prev-next-links')
        for elt in nav_link:
            if (elt.find("a") == None):
                page_suivante = None
            elif elt.find("a").text.__contains__('suivant'):
                page_suivante = "https://dicames.online" + elt.find("a")['href']     
        print(page_suivante)
        donnees_page = []
        #Tant qu'il y'a une page suivante, on recupère les données de cette page
        while page_suivante is not None:
                response = requests.get(page_suivante)
                soup = BeautifulSoup(response.content, 'html.parser')
                #donnees_page = scraper_page(url_suivante)
                for ligne in soup.find_all('tr'):
                    ligne_data = []
                    ligne_data.append(myList[0])
                    ligne_data.append(myList[1])
                    ligne_data.append(myList[3])
                    for cellule in ligne.find_all('td'):
                        valeur = cellule.text.strip()
                        ligne_data.append(valeur)
                    donnees_page.append(ligne_data)
                    #print(donnees_page)
                    
                donnees.extend(donnees_page)
                print(donnees)
                nav_link = soup.find('div', 'prev-next-links')
                links = nav_link.find_all("a")
            # On vérifie pour chaque page l'existence d'un eventuel lien vers une page suivante    
                for elt in links:
                    if elt.text.__contains__('suivant'):
                        page_suivante = "https://dicames.online" + elt["href"] 
                    else:
                        page_suivante = None
        print(donnees)
        df = pd.DataFrame(donnees, columns=['Communauté', 'Collection', 'Pays', 'Année de Publication','Titre', 'Auteur(s)' ])
        
        return df
    else:
        return None

#### La fonction data_all

Nous allons récupérer la liste des sous-communauté de chaque communauté et construire un dataframe contenant les données de ces-dernières.
La fonction data_all permet de faire cela.


In [6]:
""" La fonction data_all prend en paramètres un dataframe contenant toutes les sous_communautés d'une communauté avec leurs données afférentes.
Chaque ligne du dataframe est présentée comme ceci: (sous_communauté, pays,collection,lien_vers_la_collection). On parcourt ainsi chaque ligne
du dataframe et on recupère toutes les données de la collection pour à la fin avoir un dataframe contenant toutes les données de la communauté.  """


def data_all(sous_communaute):
    
    data_list = []
 
    for index, row in sous_communaute.iterrows():
        row = row.to_list()
        data_f = construire_df(row)
        data_list.append(data_f)

    data_communaute = pd.concat(data_list)

    data_communaute.to_csv('datas.csv', mode='a', index=False)

#### Recupérons les données communautés par communtés

- #### Pour le Burkina Faso

In [7]:
burkina_faso = liste_sous_communaute("https://dicames.online/jspui/handle/20.500.12177/3625", "Burkina Faso")

data_all(burkina_faso)

Traitement de données pour le Burkina Faso Veuillez Patienter...
None
[['Centre national de la recherche scientifique et technologique - CNRST', 'Thèses soutenues', 'Burkina Faso'], ['Centre national de la recherche scientifique et technologique - CNRST', 'Thèses soutenues', 'Burkina Faso', '2010-06-17', 'La protéine suppresseur P1 des virus de la panachure jaune du riz (Oryza sp.) et du chiendent (Imperata cylindrica) : diversité, étude fonctionnelle et applications en biotechnologies', 'Sérémé, Drissa'], ['Centre national de la recherche scientifique et technologique - CNRST', 'Thèses soutenues', 'Burkina Faso', '2017-07-26', 'Utilisation des bioindicateurs  comme outil de suivi des écosystèmes  au  Burkina Faso', 'Akoudjin, Massouroudini'], ['Centre national de la recherche scientifique et technologique - CNRST', 'Thèses soutenues', 'Burkina Faso', '2010-03-02', 'La fermentation lactique dans le procédé traditionnel de fabrication de la bière de sorgho (dolo, pito) : caractérisation

- #### Pour le Benin

In [8]:
benin = liste_sous_communaute("https://dicames.online/jspui/handle/20.500.12177/3626", "Benin")

data_all(benin)

Traitement de données pour le Benin Veuillez Patienter...
None
[["Université d'Abomey-Calavi", 'Articles publiés dans des revues à comité scientifique', 'Benin'], ["Université d'Abomey-Calavi", 'Articles publiés dans des revues à comité scientifique', 'Benin', '2019-06', 'Impact du conseil agricole privé sur l’efficacité technique des petits producteurs d’ananas au Bénin', 'Adegbidi, Anselme; Gandonou, Esaïe; Kpenavoun Chogou, Sylvain'], ["Université d'Abomey-Calavi", 'Articles publiés dans des revues à comité scientifique', 'Benin', '2019-05', 'Contrats agricoles informels et performance de la production vivrière : cas du maïs au sud du Bénin', 'Gandonou, A. Esaïe; Fafeh, Aubain; Kpenavoun Chogou, Sylvain; Adegbidi, A. Anselme'], ["Université d'Abomey-Calavi", 'Articles publiés dans des revues à comité scientifique', 'Benin', '2019-04-01', 'Cartographie  de  la  dynamique  environnementale  sur  les  parcours  naturels  des troupeaux bovins dans la Commune de Savalou au Bénin', 'Kount

- #### Pour le Cameroun

In [9]:
cameroun = liste_sous_communaute("https://dicames.online/jspui/handle/20.500.12177/3628", "Cameroun")

data_all(cameroun)

Traitement de données pour le Cameroun Veuillez Patienter...
https://dicames.online/jspui/handle/20.500.12177/6041?offset=20
[["Ecole des Sciences de la Santé de l'Université Catholique d'Afrique Centrale - (ESS-UCAC)", "IDE - Infirmier Diplômé d'État", 'Cameroun'], ["Ecole des Sciences de la Santé de l'Université Catholique d'Afrique Centrale - (ESS-UCAC)", "IDE - Infirmier Diplômé d'État", 'Cameroun', '2017', "Prévention d l'anémie par les parents des enfants de 06 à 60 mois  cas de l'hôpital catholique de Salapoumbe", 'Nzambisa, Lusau Irène'], ["Ecole des Sciences de la Santé de l'Université Catholique d'Afrique Centrale - (ESS-UCAC)", "IDE - Infirmier Diplômé d'État", 'Cameroun', '2017', "Facteurs favorisant les grossesses précoces chez les adolescentes de 15 à 19 ans du lycée bilingue d'Emana Yaoundé", 'Nke Emogo, Désiré'], ["Ecole des Sciences de la Santé de l'Université Catholique d'Afrique Centrale - (ESS-UCAC)", "IDE - Infirmier Diplômé d'État", 'Cameroun', '2017', "Facteurs l

- #### Pour le Congo

In [ ]:
congo = liste_sous_communaute("https://dicames.online/jspui/handle/20.500.12177/3631", "Congo")

data_all(congo)

- #### Pour la Cote d'Ivoire

In [ ]:
cote_divoire = liste_sous_communaute("https://dicames.online/jspui/handle/20.500.12177/3630", "Cote d'Ivoire")

data_all(cote_divoire)

- #### Pour l'Egypte

In [ ]:
egypte = liste_sous_communaute("https://dicames.online/jspui/handle/20.500.12177/3633", "Egypte")

data_all(egypte)

- #### Pour le Mali

In [ ]:
mali = liste_sous_communaute("https://dicames.online/jspui/handle/20.500.12177/3635", "Mali")

data_all(mali)

- #### Pour le Niger

In [ ]:
niger = liste_sous_communaute("https://dicames.online/jspui/handle/20.500.12177/3629", "Niger")

data_all(niger)

- #### Pour le Senegal

In [ ]:
senegal = liste_sous_communaute("https://dicames.online/jspui/handle/20.500.12177/3627", "Senegal")

data_all(senegal)

- #### Autres Pays

In [ ]:
autres_pays = liste_sous_communaute("https://dicames.online/jspui/handle/20.500.12177/3636", "Autres Pays")

data_all(autres_pays)

#### Resultat Obtenu

On obtient un fichier nommé data.csv qui contient les données brutes.
Ces dernières seront soumises à un traitement sur OpenRefine.